In [42]:
include("MDBM__types.jl")
using Plots
gr()

Plots.GRBackend()

In [49]:
ax1=Axis(-5:5.0,"x")
ax2=Axis(-7:1:7.0,"y")
ax3=Axis(-3:3.0,"z")

mdbmaxes=[ax1,ax2,ax3]

function f(x,y,z)

    pN=10.85
    [abs(x)^pN+abs(y)^pN+abs(z)^pN-2.0^pN]
end

function c(x,y,z)
    [x-sin(y)+1,z-x^3]
end

println.(([length(mdbmaxes[i].ticks) for i in 1:3]))
# @time mdbm=MDBM_Problem(f,mdbmaxes,constraint=c,memoization=false)
@time mdbm=MDBM_Problem(f,mdbmaxes,constraint=c)
@time interpolate!(mdbm,interpolationorder=0)
println(length(mdbm.ncubes))

11
15
7
  0.788294 seconds (1.50 M allocations: 77.659 MiB, 29.61% gc time)
  0.079843 seconds (158.06 k allocations: 7.464 MiB)
52


In [56]:
for kstep=1:1
# @time refine!(mdbm)
@time interpolate!(mdbm,interpolationorder=1)
# println(length(mdbm.axes[1].ticks))
# println(length(mdbmaxes[1].ticks))
# println(length(ax1.ticks))
end
# # plotlyjs()
# # unicodeplots()
x,y,z=getinterpolatedpoint(mdbm)
println.(([length(mdbmaxes[i].ticks) for i in 1:3]))
println(length(x))
scatter(x,y,z,size = (900, 900))

  0.498732 seconds (2.69 M allocations: 93.063 MiB, 30.15% gc time)
321
449
193
22734


In [ ]:
include("MDBM__types.jl")
using Profile
using ProfileView

In [ ]:
ax1=Axis(-5:5.0,"x")
ax2=Axis(-7:1:7.0,"y")

mdbmaxes=[ax1,ax2]

function f(x,y)
    [x*x+y*y-2.0*2.0]
end

function c(x,y)
    y+x
end
interporder=1;#0
mdbm0=MDBM_Problem(f,mdbmaxes,constraint=c)

refine!(mdbm0)
interpolate!(mdbm0,interpolationorder=0)

In [ ]:
#mdbm=MDBM_Problem(f,[Axis(-5:5.0,"x"),Axis(-7:1:7.0,"y")],constraint=c)
function runN!(mdbm,N)
    interpolate!(mdbm,interpolationorder=0)
    for kstep=1:N
        refine!(mdbm)
        interpolate!(mdbm,interpolationorder=0)
    end
end

In [ ]:
Profile.clear()
for i in 1:10
    mdbm=MDBM_Problem(f,[Axis(-5:5.0,"x"),Axis(-7:1:7.0,"y")],constraint=c)
    runN!(mdbm,4)
end

In [ ]:
Profile.clear()
@profile for i in 1:10
    mdbm=MDBM_Problem(f,[Axis(-5:5.0,"x"),Axis(-7:1:7.0,"y")],constraint=c)
    runN!(mdbm,4)
end

In [ ]:
ProfileView.view()

In [ ]:
include("MDBM__types.jl")
using Plots
gr()

println("-................")

ax1=Axis([-5,0,3,5],"x")
ax2=Axis(Float16,(-7:1:7.0))
ax3=Axis(-3:3.0,"z")

mdbmaxes=(ax1,ax2,ax3)
function f(x,y,z)
     [x*x+y*y+z*z-2.0*2.0]
    # [x*x+y*y+z*z-2.0*2.0,(x+y+z*2.0)]#,y<0,(x+1.5)<0]
    # [x*x+y*y+z*z-2.0*2.0,(x+y+z*2.0),y<0,(x+1.5)<0] #így is működik
end
function c(x,y,z)
    #[y,x+0.2*y+1.8,z]
    minimum([y,x+1.5,z])
end

@time mymdbm=MDBM_Problem(f,[mdbmaxes...],constraint=c)

InterporderN=1
@time interpolate!(mymdbm,interpolationorder=InterporderN)


@time for k=1:5
refine!(mymdbm)
interpolate!(mymdbm,interpolationorder=InterporderN)
println("-...==========......")
end

using Plots
gr()

x,y,z=getinterpolatedpoint(mymdbm)
println("pontins: ", length(mymdbm.ncubes))
println("function evaluation and memo: ",[length(mymdbm.fc.fvalarg),mymdbm.fc.memoryacc[1]])
scatter(x,y,z)